In [1]:
import numpy as np
from math import log

def log2(val):
    return log(val, 2)

# print a matrix for latex
def latex_matrix(A):
    for row in A:
        for ele in row[:-1]:
            print(ele, end=' & ')
        print(row[-1], end=' \\\\\n')

# pretty print for np.array 
# from https://stackoverflow.com/questions/53126305/pretty-printing-numpy-ndarrays-using-unicode-characters/53164538#53164538

def pretty_print(A):
    if A.ndim==1:
        print(A)
    else:
        w = max([len(str(s)) for s in A]) 
        print(u'\u250c' + u'\u2500' * w + u'\u2510') 
        for AA in A:
            print(' ', end='')
            print('[', end='')
            for i, AAA in enumerate(AA[:-1]):
                w1 = max([len(str(s)) for s in A[:, i]])
                print(str(AAA) + ' ' * (w1  - len(str(AAA)) + 1), end='')
            w1 = max([len(str(s)) for s in A[  :, -1]])
            print(str(AA[-1]) + ' ' * (w1 - len(str(AA[-1]))), end='')
            print(']')
        print(u'\u2514'+u'\u2500' * w + u'\u2518')  

def compare(left: set, right: set):
    if len(left) == len(right):
        for i in range(len(left)):
            if left[i] != right[i]:
                return left[i] < right[i]
    return left < right



### Generate $\mathcal{A}_n^2$

> Let $|\cdot|$ denotes cardinality and $\Delta$ denote symmetric different

In [2]:
def Delta(left: set, right: set):
    return left.symmetric_difference(right)

def Cardi(x: set):
    return len(x)

> Let $n=2^m$, $\Omega$ be a set of $m$ element such that $|\alpha_i| \leq |\alpha_{i+1}|$ and $|\alpha_i \Delta \alpha_{i+1}| \leq 2$  
> Let $\alpha_0=\{\varnothing\}$, now genereate $\Omega$

> utils func for checking $|\alpha_i| \leq |\alpha_{i+1}|$ and $|\alpha_i \Delta \alpha_{i+1}| \leq 2$  

In [3]:
def legal(alpha_i: set, alpha_i_1: set):
    return Cardi(alpha_i) <= Cardi(alpha_i_1) and Cardi(Delta(alpha_i, alpha_i_1)) <= 2

def assert_omega(ome, _m, skip=0):
    for i in range(0 + skip, len(ome) - 1):
        if not legal(ome[i], ome[i + 1]):
            print(ome[i], ome[i + 1])
        assert(legal(ome[i], ome[i + 1]))
    assert(len(ome) == 2**_m + 1)

In [4]:
from itertools import chain, combinations

# generate Omega
def insert_one_element(initial_sets: list, super_end: int) -> list:
    res = []
    for initial_set in initial_sets:
        avail_range = list(range(max(initial_set) + 1, super_end + 1))
        if len(avail_range) == 0:
            continue
        if len(res) == 0 and avail_range[0] not in initial_sets[-1]:
            avail_range.reverse()
        elif len(res) != 0 and avail_range[0] not in res[-1]:
            avail_range.reverse()
        for avail_ele in avail_range:
            if avail_ele in initial_set:
                break
            cur_res = initial_set.copy()
            cur_res.add(avail_ele)
            res.append(cur_res)
    
    return res

def create_Omega(_m: int):
    initial_sets = [{i + 1} for i in range(_m)]
    grouped_res = [initial_sets]
    for _ in range(1, _m):
        grouped_res.append(insert_one_element(grouped_res[-1], _m))

    res = [set(), set()]
    for single_res in  grouped_res:
        res.extend(single_res)
    ### the follow code is for verification
    s = list(range(1, _m + 1))
    unoredered = list(chain.from_iterable(combinations(s, r) for r in range(len(s)+1)))
    for ele in unoredered:
        assert(set(ele) in res)
    assert(len(unoredered) == len(res) - 1)
    assert_omega(res, _m)
    ### verification ends
    return res


In [40]:
# test
_test_m = 4
_test_omega = create_Omega(_test_m)
_test_omega

[set(),
 set(),
 {1},
 {2},
 {3},
 {4},
 {1, 4},
 {1, 3},
 {1, 2},
 {2, 4},
 {2, 3},
 {3, 4},
 {1, 3, 4},
 {1, 2, 3},
 {1, 2, 4},
 {2, 3, 4},
 {1, 2, 3, 4}]

> now that we have $\Omega = [a_{0}, a_{1}, ..., a_{k}]$, we can generate $A=\{\alpha_{ij}\} \in \mathcal{A}_n^2$ by:  
> $$a_{ij} = \begin{cases}
    -1,\;\alpha_j\bigcap(\alpha_{i-1}\bigcup\alpha_i)=\alpha_{i-1}\Delta\alpha_{i}\;and\;|\alpha_{i-1}\Delta\alpha_{i}|=2 \\
    (-1)^{|\alpha_{i-1}\bigcap\alpha_j| + 1},\;\alpha_{j}\bigcap(\alpha_{i-1}\bigcup\alpha_{i})\neq\varnothing\;but\;does\;not\;meet\;the\;condition\;above \\
    1,\;\alpha_j\bigcap(\alpha_{i-1}\bigcup\alpha_i)=\varnothing \\
\end{cases}
$$

In [41]:
def query_element(i: int, j: int, _omega: list) -> int:
    alpha_j = _omega[j + 1]
    alpha_i_1 = _omega[i]
    alpha_i = _omega[i + 1]

    if alpha_j.intersection(alpha_i_1.union(alpha_i)) == Delta(alpha_i_1, alpha_i) \
        and Cardi(Delta(alpha_i_1, alpha_i)) == 2:
        return -1
    elif Cardi(alpha_j.intersection(alpha_i_1.union(alpha_i))) != 0:
        return (-1)**(Cardi(alpha_i_1.intersection(alpha_j)) + 1)
    elif Cardi(alpha_j.intersection(alpha_i_1.union(alpha_i))) == 0:
        return 1
    else:
        raise ValueError("Undefined behavior!")
    
def create_A(_omega, _m):
    A_mat = np.zeros((2**_m, 2**_m))
    for i in range(A_mat.shape[0]):
        for j in range(A_mat.shape[1]):
            A_mat[i, j] = query_element(i, j, _omega)
    return A_mat

In [42]:
# test
A_mat = create_A(_test_omega, _test_m)
pretty_print(A_mat.astype(int))

┌─────────────────────────────────────────────────┐
 [1 1  1  1  1  1  1  1  1  1  1  1  1  1  1  1 ]
 [1 -1 1  1  1  -1 -1 -1 1  1  1  -1 -1 -1 1  -1]
 [1 1  -1 1  1  1  1  -1 -1 -1 1  1  -1 -1 -1 -1]
 [1 1  1  -1 1  1  -1 1  1  -1 -1 -1 -1 1  -1 -1]
 [1 1  1  1  -1 -1 1  1  -1 1  -1 -1 1  -1 -1 -1]
 [1 -1 1  1  1  1  -1 -1 1  1  1  1  -1 1  1  1 ]
 [1 1  1  -1 1  -1 1  1  1  -1 -1 -1 1  -1 -1 -1]
 [1 1  -1 1  1  1  -1 1  -1 -1 1  -1 -1 1  -1 -1]
 [1 1  1  1  -1 -1 1  -1 1  1  -1 -1 -1 -1 1  -1]
 [1 1  1  -1 1  1  -1 1  -1 1  -1 -1 1  -1 -1 -1]
 [1 1  1  1  -1 -1 1  1  -1 -1 1  1  -1 -1 -1 -1]
 [1 -1 1  1  1  1  1  -1 1  1  -1 -1 1  1  -1 -1]
 [1 1  -1 1  1  -1 -1 1  -1 1  -1 1  -1 -1 -1 1 ]
 [1 1  1  1  -1 1  -1 -1 1  -1 -1 -1 1  -1 -1 1 ]
 [1 1  1  -1 1  -1 -1 -1 -1 1  1  -1 -1 1  -1 1 ]
 [1 -1 1  1  1  1  1  1  -1 -1 -1 -1 -1 -1 1  1 ]
└─────────────────────────────────────────────────┘


### Check $A = LQ$

> Let $Q$ be a $n$ by $n$ matrix given by $q_{ij} = (-1)^{|\alpha_i \bigcap \alpha_j|}$, $Q$ is a symmetric Hadamard matrix, that is $Q^2=QQ^T=nI_n$  
> now we check if $Q$ is a symmetric Hadamard matrix  

In [43]:
def get_Q(_omega, _n):
    Q_mat = np.zeros((_n, _n))
    for i in range(_n):
        for j in range(_n):
            Q_mat[i, j] = (-1) ** Cardi(_omega[i + 1].intersection(_omega[j + 1]))
    return np.matrix(Q_mat)

Q_mat = get_Q(_test_omega, 2**_test_m)
pretty_print(np.array((Q_mat).astype(int)))
pretty_print(np.array((Q_mat * Q_mat).astype(int)))

┌─────────────────────────────────────────────────┐
 [1 1  1  1  1  1  1  1  1  1  1  1  1  1  1  1 ]
 [1 -1 1  1  1  -1 -1 -1 1  1  1  -1 -1 -1 1  -1]
 [1 1  -1 1  1  1  1  -1 -1 -1 1  1  -1 -1 -1 -1]
 [1 1  1  -1 1  1  -1 1  1  -1 -1 -1 -1 1  -1 -1]
 [1 1  1  1  -1 -1 1  1  -1 1  -1 -1 1  -1 -1 -1]
 [1 -1 1  1  -1 1  -1 -1 -1 1  -1 1  -1 1  -1 1 ]
 [1 -1 1  -1 1  -1 1  -1 1  -1 -1 1  1  -1 -1 1 ]
 [1 -1 -1 1  1  -1 -1 1  -1 -1 1  -1 1  1  -1 1 ]
 [1 1  -1 1  -1 -1 1  -1 1  -1 -1 -1 -1 1  1  1 ]
 [1 1  -1 -1 1  1  -1 -1 -1 1  -1 -1 1  -1 1  1 ]
 [1 1  1  -1 -1 -1 -1 1  -1 -1 1  1  -1 -1 1  1 ]
 [1 -1 1  -1 -1 1  1  -1 -1 -1 1  -1 1  1  1  -1]
 [1 -1 -1 -1 1  -1 1  1  -1 1  -1 1  -1 1  1  -1]
 [1 -1 -1 1  -1 1  -1 1  1  -1 -1 1  1  -1 1  -1]
 [1 1  -1 -1 -1 -1 -1 -1 1  1  1  1  1  1  -1 -1]
 [1 -1 -1 -1 -1 1  1  1  1  1  1  -1 -1 -1 -1 1 ]
└─────────────────────────────────────────────────┘
┌─────────────────────────────────────────────────┐
 [16 0  0  0  0  0  0  0  0  0  0  0  0  0  

> And verify matrix $L = AQ^{-1}$ is a lower triangular matrix

In [44]:
pretty_print(np.array(np.matrix(A_mat) * np.matrix(Q_mat).I))

┌──────────────────────────────────────────────────────────────────────────────────────────────────────────────────┐
 [1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0    0.0  ]
 [0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0    0.0  ]
 [0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0    0.0  ]
 [0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0    0.0  ]
 [0.0   0.0   0.0   0.0   1.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0    0.0  ]
 [0.5   0.5   0.0   0.0   -0.5  0.5   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0    0.0  ]
 [0.0   0.0   0.0   0.5   0.5   -0.5  0.5   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0    0.0  ]
 [0.0   0.0   0.5   0.5   0.0   0.0   -0.5  0.5   0.0   0.0   0.0   0.0   0.0   0.0   0.0    0.0  ]
 [0.0   0.5   0.0   0.0   0.5   0.0   0.0   -0.5  0.5   0.0   0.0   0.0   0.0   0.0

### Generate $\mathcal{A}_{n - 1}^1$

> Let $B\in\mathcal{A}_{n - 1}^1$, $\Phi(B)\in\mathcal{A}_{n}^2\;$:
> $$ \Phi(B) = \left(\begin{array}{cc} 
1 & 1_{n-1}\\
-1^T_{n-1} & 2B-J_{n-1}
\end{array}\right)
> $$
>
> notice that the $A_2 \in \mathcal{A}_n^2$ we have has it's first column as:
> $$ A_2 = \Phi(B) = \left(\begin{array}{cc} 
1\\
1^T_{n-1}
\end{array}\right)
> $$
> we need to multiply $\{\alpha_{ij}\}_{2\le i\le n, 2\le j\le n} \in \mathcal{A}_n^2$ with $-1$  
> so we can generate matrix $A_1 \in \mathcal{A}_{n - 1}^1$ with $A_2 = \{\alpha_{ij}\} \in \mathcal{A}_n^2$ using the following relation:    
> $$A_1 = \frac{1}{2}(J_{n-1}-\{\alpha_{ij}\}_{2\le i\le n, 2\le j\le n})$$

In [45]:
def create_A_1_mat(A_2_mat):
    
    A_1_mat = (np.ones(A_2_mat.shape[0] - 1) - A_2_mat[1:, 1:]) * 0.5
    assert((A_1_mat.max() == 1 and A_1_mat.min() == 0) if A_1_mat.shape[0] > 1 else True)
    return A_1_mat


In [46]:
# test
A_1 = create_A_1_mat(A_mat).astype(int)
pretty_print(A_1)

┌───────────────────────────────┐
 [1 0 0 0 1 1 1 0 0 0 1 1 1 0 1]
 [0 1 0 0 0 0 1 1 1 0 0 1 1 1 1]
 [0 0 1 0 0 1 0 0 1 1 1 1 0 1 1]
 [0 0 0 1 1 0 0 1 0 1 1 0 1 1 1]
 [1 0 0 0 0 1 1 0 0 0 0 1 0 0 0]
 [0 0 1 0 1 0 0 0 1 1 1 0 1 1 1]
 [0 1 0 0 0 1 0 1 1 0 1 1 0 1 1]
 [0 0 0 1 1 0 1 0 0 1 1 1 1 0 1]
 [0 0 1 0 0 1 0 1 0 1 1 0 1 1 1]
 [0 0 0 1 1 0 0 1 1 0 0 1 1 1 1]
 [1 0 0 0 0 0 1 0 0 1 1 0 0 1 1]
 [0 1 0 0 1 1 0 1 0 1 0 1 1 1 0]
 [0 0 0 1 0 1 1 0 1 1 1 0 1 1 0]
 [0 0 1 0 1 1 1 1 0 0 1 1 0 1 0]
 [1 0 0 0 0 0 0 1 1 1 1 1 1 0 0]
└───────────────────────────────┘


In [47]:
from scipy.optimize import minimize
from itertools import combinations
from time import time

class CalculateDistanceBetweenPointAndPolytope:
    # Function to calculate the Euclidean distance
    def euclidean_distance(self, x, point):
        return np.linalg.norm(x - point)

    # Function to minimize: distance between the chosen point and the convex combination of the remaining points
    def distance_to_polytope(self, lambda_vals, remaining_points, point):
        convex_combination = np.dot(lambda_vals, remaining_points)
        return self.euclidean_distance(convex_combination, point)

    def calculate_distance(self, matrix, selected_index):
        # Extract the selected point
        selected_point = matrix[:, selected_index]
        
        # Extract the remaining points (excluding the selected one)
        remaining_indices = [i for i in range(matrix.shape[1]) if i != selected_index]
        remaining_points = matrix[:, remaining_indices]
        
        # Initial guess for lambda values (uniformly distributed)
        initial_lambda = np.ones(len(remaining_indices)) / len(remaining_indices)
        
        # Constraints: lambda_i >= 0 and sum(lambda) = 1
        constraints = [{'type': 'eq', 'fun': lambda lambda_vals: np.sum(lambda_vals) - 1},
                    {'type': 'ineq', 'fun': lambda lambda_vals: lambda_vals}]  # lambda_i >= 0
        
        # Minimize the distance to the convex hull (polytope)
        result = minimize(
            self.distance_to_polytope,
            initial_lambda,
            args=(remaining_points.T, selected_point),
            constraints=constraints,
            method='SLSQP'
        )
        
        # The minimum distance
        return result.fun


class CalculateDistanceBetweenHulls:
    # Function to calculate the Euclidean distance between two points
    def euclidean_distance_between_points(self, x, y):
        return np.linalg.norm(x - y)

    # Function to minimize: distance between points from convex hulls of S and T
    def distance_between_hulls(self, lambda_s, lambda_t, points_s, points_t):
        convex_comb_s = np.dot(lambda_s, points_s)
        convex_comb_t = np.dot(lambda_t, points_t)
        return self.euclidean_distance_between_points(convex_comb_s, convex_comb_t)

    def calculate_hull_distance(self, matrix, S_indices, T_indices):
        points_S = matrix[:, S_indices]
        points_T = matrix[:, T_indices]
        
        # Initial guesses for lambda values (uniformly distributed)
        initial_lambda_s = np.ones(len(S_indices)) / len(S_indices)
        initial_lambda_t = np.ones(len(T_indices)) / len(T_indices)
        
        # Constraints: lambda_i >= 0 and sum(lambda) = 1
        constraints_s = [{'type': 'eq', 'fun': lambda lambda_vals: np.sum(lambda_vals[:len(S_indices)]) - 1},
                        {'type': 'ineq', 'fun': lambda lambda_vals: lambda_vals[:len(S_indices)]}]  # lambda_i >= 0
        
        constraints_t = [{'type': 'eq', 'fun': lambda lambda_vals: np.sum(lambda_vals[len(S_indices):]) - 1},
                        {'type': 'ineq', 'fun': lambda lambda_vals: lambda_vals[len(S_indices):]}]  # lambda_i >= 0
        constraints = constraints_s + constraints_t

        # Minimize the distance between the convex hulls of S and T
        result = minimize(
            lambda lambda_vals: self.distance_between_hulls(
                lambda_vals[:len(S_indices)], lambda_vals[len(S_indices):], points_S.T, points_T.T
            ),
            np.concatenate([initial_lambda_s, initial_lambda_t]),
            constraints=constraints,
            method='SLSQP',
            bounds=[(0, 1)] * (len(S_indices) + len(T_indices))
        )
        
        # The minimum distance
        min_distance = result.fun
        # lambda_s_opt = result.x[:len(S_indices)]
        # lambda_t_opt = result.x[len(S_indices):]
        
        return min_distance

    def calculate_all_partitions_and_distances(self, matrix):
        d_plus_1 = matrix.shape[1]  # Total number of points (d+1)
        points = list(range(d_plus_1))   # The indices of points
        
        # Collect all possible partitions (S, T) of the d+1 points
        distances = []
        
        # Iterate over all possible sizes of S
        for s_size in range(2, d_plus_1 // 2 + 1):  # S must contain at least 2 point, and so must T
            if s_size * 2 < d_plus_1:
                for S_indices in combinations(points, s_size):
                    T_indices = [p for p in points if p not in S_indices]
                    start_time = time()
                    distance = self.calculate_hull_distance(matrix, S_indices, T_indices)
                    end_time = time()
                    print(f"Partition S: {S_indices}, Partition T: {tuple(T_indices)}, Distance: {distance}, Time: {end_time - start_time}")
                    distances.append((S_indices, T_indices, distance))
            else: # s_size * 2 == d_plus_1
                combs = list(combinations(points, s_size))
                for S_indices in combs[:len(combs) // 2]:
                    T_indices = [p for p in points if p not in S_indices]
                    start_time = time()
                    distance = self.calculate_hull_distance(matrix, S_indices, T_indices)
                    end_time = time()
                    print(f"Partition S: {S_indices}, Partition T: {tuple(T_indices)}, Distance: {distance}, Time: {end_time - start_time}")
                    distances.append((S_indices, T_indices, distance))

        return distances

def beautiful_print(results):
    # markdown_output = "| S | T | Distance |\n"
    # markdown_output += "|---|---|----------|\n"

    # for result in results:
    #     s_values = ','.join(map(str, result['S']))  # Convert tuple S to comma-separated string
    #     t_values = ','.join(map(str, result['T']))  # Convert tuple T to comma-separated string
    #     distance_value = result['Distance']
        
    #     # Append row to the markdown table
    #     markdown_output += f"| {s_values} | {t_values} | {distance_value} |\n"
    
    # print(markdown_output)

    # Generate TSV table with three columns, using \t as the separator
    tsv_output = "S\tT\tDistance\n"

    for result in results:
        s_values = ','.join(map(str, result['S']))  # Treat tuple S as a string
        t_values = ','.join(map(str, result['T']))  # Treat tuple T as a string
        distance_value = result['Distance']
        
        # Append row to the TSV table
        tsv_output += f"{s_values}\t{t_values}\t{distance_value}\n"

    with open(f'output_{A_1.shape[0]}.csv', 'w') as csv_file:
        csv_file.write(tsv_output)


d = A_1.shape[0]
matrix = np.concatenate((np.zeros((d, 1)), A_1), axis=1)
print("Matrix:")
print(matrix)

results = []

for selected_idx in range(matrix.shape[1]):
    start_time = time()
    distance = CalculateDistanceBetweenPointAndPolytope().calculate_distance(matrix, selected_idx)
    end_time = time()
    print(f"Partition S: {(selected_idx)}, Partition T: {tuple(set([_ for _ in range(d + 1)]).difference([selected_idx]))}, Distance: {distance}, Time: {end_time - start_time}")
    results.append({'S': tuple([selected_idx]), 'T': tuple(set([_ for _ in range(d + 1)]).difference([selected_idx])), 'Distance': distance})

distances = CalculateDistanceBetweenHulls().calculate_all_partitions_and_distances(matrix)
for S, T, distance in distances:
    # print(f"Partition S: {S}, Partition T: {tuple(T)}, Distance: {distance}")
    results.append({'S': S, 'T': tuple(T), 'Distance': distance})

beautiful_print(results)

min_distance = min(results, key=lambda x: x['Distance'])
print(f"The minimum distance is {min_distance['Distance']} for partitions S={min_distance['S']} and T={min_distance['T']}")

Matrix:
[[0. 1. 0. 0. 0. 1. 1. 1. 0. 0. 0. 1. 1. 1. 0. 1.]
 [0. 0. 1. 0. 0. 0. 0. 1. 1. 1. 0. 0. 1. 1. 1. 1.]
 [0. 0. 0. 1. 0. 0. 1. 0. 0. 1. 1. 1. 1. 0. 1. 1.]
 [0. 0. 0. 0. 1. 1. 0. 0. 1. 0. 1. 1. 0. 1. 1. 1.]
 [0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 1. 0. 0. 0.]
 [0. 0. 0. 1. 0. 1. 0. 0. 0. 1. 1. 1. 0. 1. 1. 1.]
 [0. 0. 1. 0. 0. 0. 1. 0. 1. 1. 0. 1. 1. 0. 1. 1.]
 [0. 0. 0. 0. 1. 1. 0. 1. 0. 0. 1. 1. 1. 1. 0. 1.]
 [0. 0. 0. 1. 0. 0. 1. 0. 1. 0. 1. 1. 0. 1. 1. 1.]
 [0. 0. 0. 0. 1. 1. 0. 0. 1. 1. 0. 0. 1. 1. 1. 1.]
 [0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 1. 1. 0. 0. 1. 1.]
 [0. 0. 1. 0. 0. 1. 1. 0. 1. 0. 1. 0. 1. 1. 1. 0.]
 [0. 0. 0. 0. 1. 0. 1. 1. 0. 1. 1. 1. 0. 1. 1. 0.]
 [0. 0. 0. 1. 0. 1. 1. 1. 1. 0. 0. 1. 1. 0. 1. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 1. 1. 1. 1. 1. 1. 0. 0.]]
Partition S: 0, Partition T: (1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15), Distance: 0.9607689230996417, Time: 0.011040925979614258
Partition S: 1, Partition T: (0, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15), Dista